# **Final Project: Can Signals Beat the Benchmark?**
## MBAI 5300G - Programming and Data Processing


## Data Ingestion


In [1]:
# Import required libraries
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas_ta as ta
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

# Initialize ticker object for ZQQ benchmark
zqq = yf.Ticker('ZQQ.TO')

# Get top 10 holdings in ZQQ and extract tickers
holdings_df = zqq.funds_data.top_holdings
tickers = holdings_df.index.to_list()
tickers.append('ZQQ.TO')

# Download historical data over L10Y for all tickers
data = yf.download(tickers, period = '10y', group_by = 'ticker')

# Create dict of dfs containing historical data for each ticker
all_data = {}
for ticker in tickers:
    all_data[ticker] = data[ticker].dropna(how = 'all').copy()

# Split benchmark and individual stocks
benchmark_df = all_data['ZQQ.TO']
stock_dfs = {ticker: df for ticker, df in all_data.items() if ticker != 'ZQQ.TO'}


/tmp/ipython-input-3904912913.py:20: FutureWarning: YF.download() has changed argument auto_adjust default to True
  data = yf.download(tickers, period = '10y', group_by = 'ticker')
[*********************100%***********************]  11 of 11 completed


## Exploratory Data Analysis


In [2]:
# Get start and end dates for subtitle and format appropriately
start_date = benchmark_df.index.min().strftime('%B %d, %Y')
end_date = benchmark_df.index.max().strftime('%B %d, %Y')

# Plot ZQQ price over L10Y
fig = px.line(
    data_frame = benchmark_df,
    x = benchmark_df.index,
    y = 'Close',
    template = 'simple_white'
)

fig.update_layout(
    yaxis_title = 'Close Price ($)',
    title_text = f'Close Price of ZQQ<br><sup>Last 10 Years: {start_date} – {end_date}</sup>'
)

fig.show()


In [3]:
# Sort holdings df asc
holdings_df.sort_values(by = 'Holding Percent', inplace = True)

# Get today's date for subtitle and format appropriately
today = pd.Timestamp.now().strftime('%B %d, %Y')

# Visualize top 10 holdings in ZQQ
fig = px.bar(
    data_frame = holdings_df,
    x = 'Holding Percent',
    y = holdings_df.index,
    orientation = 'h',
    template = 'simple_white'
)

fig.update_layout(
    yaxis_title = '',
    xaxis = dict(
        title = 'Allocation (%)',
        tickformat = '.0%'
    ),
    title_text = f'Top 10 Holdings in ZQQ by Allocation<br><sup>As of {today}</sup>'
)

# Add data labels w/ .2% formatting
fig.update_traces(
    texttemplate = '%{x:.2%}',
    textposition = 'inside',
    insidetextanchor = 'end',
    textfont = dict(color = 'white')
)

fig.show()


In [4]:
# Get tickers of individual stocks for plotting
plot_tickers = list(stock_dfs.keys())

# Create small multiples to visualize price trends of all individual stocks over L10Y
fig = make_subplots(
    rows = 2,
    cols = 5,
    subplot_titles = plot_tickers,
    vertical_spacing = 0.15,
    horizontal_spacing = 0.03
)

# Create subplot for each ticker
for i, ticker in enumerate(plot_tickers):
    row = (i // 5) + 1
    col = (i % 5) + 1

    df = stock_dfs[ticker]

    fig.add_trace(
        go.Scatter(
            x = df.index,
            y = df['Close'],
            mode = 'lines',
            name = ticker
        ),
    row = row,
    col = col
    )

fig.update_layout(
    title_text = 'Portfolio Constituents: 10-Year Close Price History',
    title_x = 0.5,
    showlegend = False,
    template = 'simple_white'
)

# Clean up axes
fig.update_xaxes(
    showticklabels = False,
    ticks = '',
)

fig.update_yaxes(
    showticklabels = False,
    ticks = '',
)

fig.show()


## Backtesting Simulation


### Benchmark Initialization


In [5]:
# Compute benchmark daily returns
benchmark_df['benchmark_daily_return'] = benchmark_df['Close'].pct_change()


### Helper Functions


In [6]:
# Define function to plot equity curves for strategy vs. benchmark
def plot_equity_curves(strategy_returns, benchmark_returns, strategy_name = 'Strategy'):
    """
    Plots cumulative equity curves for a given trading strategy vs. a benchmark.

    Parameters:
    -----------
        - strategy_returns (pd.Series): Daily returns of strategy.
        - benchmark_returns (pd.Series): Daily returns of benchmark.
        - strategy_name (str): Name of strategy. Default is "Strategy".

    Returns:
    --------
        - None: Does not have a return value. Generates and shows plot as side effect.
    """

    # Align strategy and benchmark series into df
    plotting_df = pd.concat([strategy_returns, benchmark_returns], axis = 1, join = 'inner') # Inner join to ensure only comparing intersection of dates
    plotting_df.columns = [strategy_name, 'Benchmark']
    plotting_df = plotting_df.dropna()

    # Compute cumulative returns
    cumulative_returns = (1 + plotting_df).cumprod() - 1

    # Get start and end dates for subtitle and format appropriately
    start_date = plotting_df.index.min().strftime('%B %d, %Y')
    end_date = plotting_df.index.max().strftime('%B %d, %Y')

    # Get total cumulative return at end of backtest for annotations
    strategy_total = cumulative_returns[strategy_name].iloc[-1]
    benchmark_total = cumulative_returns['Benchmark'].iloc[-1]

    # Get last date and compute annotation position accordingly
    last_date = plotting_df.index[-1]
    annotation_date = last_date + pd.Timedelta(days = len(plotting_df) * 0.01) # Offset annotations by 1% for readability

    # Create fig object
    fig = go.Figure()

    # Plot strategy line
    fig.add_trace(go.Scatter(
        x = cumulative_returns.index,
        y = cumulative_returns[strategy_name],
        mode = 'lines',
        name = strategy_name,
    ))

    # Plot benchmark line
    fig.add_trace(go.Scatter(
        x = cumulative_returns.index,
        y = cumulative_returns['Benchmark'],
        mode = 'lines',
        name = 'ZQQ Benchmark',
    ))

    # Add annotations for total cumulative returns
    fig.add_annotation(
        x = annotation_date,
        y = strategy_total,
        text = f'{strategy_total:.1%}',
        showarrow = False,
        xanchor = 'left',
        font = dict(
            color = '#1f77b4',
            family = 'Arial Black, sans-serif'
        )
    )

    fig.add_annotation(
        x = annotation_date,
        y = benchmark_total,
        text = f'{benchmark_total:.1%}',
        showarrow = False,
        xanchor = 'left',
        font = dict(
            color = '#ff7f0e',
            family = 'Arial Black, sans-serif'
        )
    )

    # Refine layout
    fig.update_layout(
        title = f'{strategy_name} vs. Benchmark (Cumulative Return)<br><sup>Last 10 Years: {start_date} – {end_date}</sup>',
        xaxis_title = 'Date',
        yaxis_title = 'Cumulative Return (%)',
        yaxis_tickformat = '.0%',
        template = 'simple_white',
        legend = dict(
            orientation = 'h',
            yanchor = 'bottom',
            y = 1.02,
            xanchor = 'center',
            x = 0.5
        )
    )

    fig.show()


In [7]:
# Define function to eval strategy performance vs. benchmark across pertinent metrics
def evaluate_strategy(strategy_returns, benchmark_returns, strategy_name = 'Strategy', trading_days = 252, risk_free_rate = 0.0):
    """
    Computes key performance metrics for a given trading strategy and compares them to a benchmark.

    Parameters:
    -----------
        - strategy_returns (pd.Series): Daily returns of strategy.
        - benchmark_returns (pd.Series): Daily returns of benchmark.
        - strategy_name (str): Name of strategy. Default is "Strategy".
        - trading_days (int): Number of trading days per year for annualized computations. Default is 252.
        - risk_free_rate (float): Annualized risk-free rate in decimal form. Default is 0.0.

    Returns:
    --------
        - pd.DataFrame: Comparison table containing all computed metrics.
    """

    # Align strategy and benchmark series into df
    aligned_df = pd.concat([strategy_returns, benchmark_returns], axis = 1, join = 'inner') # Inner join to ensure only comparing intersection of dates
    aligned_df.columns = [strategy_name, 'Benchmark']
    aligned_df = aligned_df.dropna()

    # Compute cumulative returns
    cumulative_returns = (1 + aligned_df).cumprod() - 1

    # Compute total returns over back-test period
    total_return = cumulative_returns.iloc[-1]

    # Compute avg daily return
    avg_daily_return = aligned_df.mean()

    # Compute annualized return
    annualized_return = avg_daily_return * trading_days

    # Compute annualized volatility
    annualized_volatility = aligned_df.std() * np.sqrt(trading_days)

    # Compute Sharpe ratio
    sharpe_ratio = (annualized_return - risk_free_rate) / annualized_volatility

    # Compute max drawdown
    daily_cum = (1 + aligned_df).cumprod()
    rolling_max = daily_cum.cummax()
    drawdown = (daily_cum / rolling_max) - 1
    max_drawdown = drawdown.min()

    # Compute Calmar ratio
    calmar_ratio = annualized_return / abs(max_drawdown)

    # Compute daily win rate (% of days w/ positive returns)
    win_rate = (aligned_df > 0).mean()

    # Compute monthly win rate (% of months w/ positive returns)
    monthly_returns = aligned_df.resample('ME').sum() # If running older version of pandas, may need to specify 'M' for month rather than 'ME' for month end
    pct_pos_months = (monthly_returns > 0).mean()

    # Compile results in dict
    metrics = {
        'Total Return': total_return,
        'Annualized Return': annualized_return,
        'Annualized Volatility': annualized_volatility,
        'Sharpe Ratio': sharpe_ratio,
        'Max Drawdown': max_drawdown,
        'Calmar Ratio': calmar_ratio,
        'Daily Win Rate': win_rate,
        'Monthly Win Rate': pct_pos_months
    }

    # Convert dict to transposed df
    metrics_df = pd.DataFrame(metrics).T
    metrics_df = metrics_df.reset_index().rename(columns = {'index': 'Metric'})

    return metrics_df


In [8]:
# Install great_tables if required: pip install great_tables
# Import required functions
from great_tables import GT, style, loc

# Define lists of metrics for each format type
percent_metrics = [
    'Total Return',
    'Annualized Return',
    'Annualized Volatility',
    'Max Drawdown',
    'Daily Win Rate',
    'Monthly Win Rate'
]

float_metrics = [
    'Sharpe Ratio',
    'Calmar Ratio'
]

# Helper function to create formatted table
def create_eval_table(performance_df, strategy_name):
    """
    Creates a formatted great_tables table from performance DataFrame.
    """
    data_cols = performance_df.columns[1:].tolist()

    return (
        GT(performance_df)
        .tab_header(
            title = strategy_name,
            subtitle = 'Strategy Performance vs. Benchmark'
        )
        .fmt_percent(
            columns = data_cols,
            decimals = 2,
            rows = lambda x: x['Metric'].isin(percent_metrics)
        )
        .fmt_number(
            columns = data_cols,
            decimals = 2,
            rows = lambda x: x['Metric'].isin(float_metrics)
        )
    )


### Trading Strategy 1: EMA Crossover (12/26) - Brennan


In [9]:
# Define function to run EMA Crossover strategy
def run_ema_strategy(stock_dfs, fast_period = 12, slow_period = 26):
    """
    Executes an EMA Crossover strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when fast EMA > slow EMA.
        - Sell (cash/flat position) when fast EMA <= slow EMA.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - fast_period (int): Lookback period for fast EMA in days. Default is 12.
        - slow_period (int): Lookback period for slow EMA in days. Default is 26.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under EMA Crossover strategy.
    """

    # Initialize dict to store EMA Crossover strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        # Copy df to leave orig unmodified
        df = df.copy()

        # Compute EMAs
        df['ema_fast'] = df['Close'].ewm(span = fast_period, adjust = False).mean()
        df['ema_slow'] = df['Close'].ewm(span = slow_period, adjust = False).mean()

        # Generate signals based on EMA Crossover, where 1 = long and 0 = flat
        df['signal'] = (df['ema_fast'] > df['ema_slow']).astype(int)

        # Compute position for trade execution, where 1 = long and 0 = flat
        df['position'] = df['signal'].shift(1).fillna(0) # Shift forward to avoid look-ahead bias when executing trades

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute daily returns of EMA Crossover strategy
        df['strategy_return'] = df['stock_return'] * df['position'] # Daily returns of underlying stock are captured (or not) based on position

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis = 1)

    return portfolio_daily_returns


In [10]:
# Execute EMA Crossover strategy
ema_portfolio_returns = run_ema_strategy(
    stock_dfs = stock_dfs,
    fast_period = 12,
    slow_period = 26
)

# Eval EMA Crossover strategy vs. benchmark
ema_performance_df = evaluate_strategy(
    strategy_returns = ema_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'EMA Crossover (12/26)',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
ema_eval_table = create_eval_table(ema_performance_df, 'EMA Crossover (12/26)')
ema_eval_table


GT(_tbl_data=                  Metric  EMA Crossover (12/26)  Benchmark
0           Total Return               5.470668   3.561391
1      Annualized Return               0.205182   0.181146
2  Annualized Volatility               0.167106   0.226756
3           Sharpe Ratio               1.227857   0.798860
4           Max Drawdown              -0.231750  -0.392813
5           Calmar Ratio               0.885359   0.461151
6         Daily Win Rate               0.525995   0.556052
7       Monthly Win Rate               0.625000   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3edac90>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='EMA Crossover (12/26)', type=<ColInfoTypeEnum.default: 1>, column_label='EMA Crossover (12/26)', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28c02d73e0>, _spanners=Spanners([]), _heading=Heading(title='EMA Crossover (12/26)', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3ddd820>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b33d3a70>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b33d3ad0>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3d0af00>, <great_tables._gt_data.FormatInfo object at 0x7c28b3d27260>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), tab

In [11]:
# Visualize EMA Crossover strategy vs. benchmark (equity curves)
plot_equity_curves(ema_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'EMA Crossover (12/26)')


### Trading Strategy 2: The Filter System (5% Threshold)

In [12]:
# Define function to run Filter System strategy
def run_filter_strategy(stock_dfs, threshold_pct = 0.05):
    """
    Executes the "Filter System" strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when the close price has moved up from its most recent low by threshold_pct.
        - Sell (cash/flat position) when the close price has moved down from its most recent high by threshold_pct.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - threshold_pct (float): Percentage move required to trigger trade signal. Default is 0.05 (5%).

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under "Filter System" strategy.
    """

    # Initialize dict to store Filter System strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        # Copy df to leave orig unmodified
        df = df.copy()

        # Extract prices as numpy array for efficiency
        prices = df['Close'].values
        day_count = len(prices)

        # Initialize array to capture signals, where 1 = long and 0 = flat
        signals = np.zeros(day_count)

        # Initialize vars to track state of strategy
        position = 0 # Start flat
        anchor_price = prices[0] # Track the most recent extreme price (low/high)

        # Iterate through days (skipping first) to generate signals based on Filter System
        for i in range(1, day_count):
            price = prices[i]

            # If flat ...
            if position == 0:
                # If price has dropped lower, update anchor w/ new low
                if price < anchor_price:
                    anchor_price = price
                # If price has risen by threshold_pct from most recent low, generate buy signal and update anchor w/ new high
                elif price >= anchor_price * (1 + threshold_pct):
                    position = 1
                    anchor_price = price
            # If long ...
            elif position == 1:
                # If price has risen higher, update anchor w/ new high
                if price > anchor_price:
                    anchor_price = price
                # If price has dropped by threshold_pct from most recent high, generate sell signal and update anchor w/ new low
                elif price <= anchor_price * (1 - threshold_pct):
                    position = 0
                    anchor_price = price

            # Record signal for the day
            signals[i] = position

        # Assign signals array back to df
        df['signal'] = signals

        # Compute position for trade execution, where 1 = long and 0 = flat
        df['position'] = df['signal'].shift(1).fillna(0) # Shift forward to avoid look-ahead bias when executing trades

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute daily returns of Filter System strategy
        df['strategy_return'] = df['stock_return'] * df['position'] # Daily returns of underlying stock are captured (or not) based on position

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis = 1)

    return portfolio_daily_returns


In [13]:
# Execute Filter System strategy
filter_portfolio_returns = run_filter_strategy(
    stock_dfs = stock_dfs,
    threshold_pct = 0.05
)

# Eval Filter System strategy vs. benchmark
filter_performance_df = evaluate_strategy(
    strategy_returns = filter_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Filter System (5% Threshold)',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
filter_eval_table = create_eval_table(filter_performance_df, 'Filter System (5% Threshold)')
filter_eval_table


GT(_tbl_data=                  Metric  Filter System (5% Threshold)  Benchmark
0           Total Return                      4.486743   3.561391
1      Annualized Return                      0.189956   0.181146
2  Annualized Volatility                      0.176424   0.226756
3           Sharpe Ratio                      1.076701   0.798860
4           Max Drawdown                     -0.312060  -0.392813
5           Calmar Ratio                      0.608714   0.461151
6         Daily Win Rate                      0.536556   0.556052
7       Monthly Win Rate                      0.591667   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28c0046e10>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Filter System (5% Threshold)', type=<ColInfoTypeEnum.default: 1>, column_label='Filter System (5% Threshold)', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28c0178d70>, _spanners=Spanners([]), _heading=Heading(title='Filter System (5% Threshold)', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3b57a40>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3b579e0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3b57980>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3b57680>, <great_tables._gt_data.FormatInfo object at 0x7c28b3b57860>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_borde

In [14]:
# Visualize Filter System strategy vs. benchmark (equity curves)
plot_equity_curves(filter_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Filter System (5% Threshold)')


### Trading Strategy 3: Comparative Relative Strength (50-Day MA) - Brennan


In [15]:
# Define function to run Comparative Relative Strength strategy
def run_rs_strategy(stock_dfs, benchmark_prices, ma_period = 50):
    """
    Executes a Comparative Relative Strength strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Compute the Price Ratio = Stock Price / Benchmark Price.
        - Compute the Moving Average (MA) of the Price Ratio over the specified ma_period.
        - Buy (long position) when Price Ratio > MA (i.e., stock is outperforming benchmark trend).
        - Sell (cash/flat position) when Price Ratio <= MA (i.e., stock is underperforming benchmark trend).

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - benchmark_prices (pd.Series): Series containing close prices of benchmark.
        - ma_period (int): Lookback period for moving average of price ratio in days. Default is 50.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under RS strategy.
    """

    # Initialize dict to store RS strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        # Copy df to leave orig unmodified
        df = df.copy()

        # Align CAD benchmark to US stock's calendar and fill any Canadian holidays w/ previous day's benchmark close
        df['benchmark_close'] = benchmark_prices.reindex(df.index, method = 'ffill')

        # Compute RS ratio
        df['rs_ratio'] = df['Close'] / df['benchmark_close']

        # Compute moving avg of RS ratio
        df['rs_ratio_ma'] = df['rs_ratio'].rolling(window = ma_period).mean()

        # Generate signals based on RS, where 1 = long and 0 = flat
        df['signal'] = (df['rs_ratio'] > df['rs_ratio_ma']).astype(int)

        # Compute position for trade execution, where 1 = long and 0 = flat
        df['position'] = df['signal'].shift(1).fillna(0) # Shift forward to avoid look-ahead bias when executing trades

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute daily returns of RS strategy
        df['strategy_return'] = df['stock_return'] * df['position'] # Daily returns of underlying stock are captured (or not) based on position

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis = 1)

    return portfolio_daily_returns


In [16]:
# Execute Comparative RS strategy
rs_portfolio_returns = run_rs_strategy(
    stock_dfs = stock_dfs,
    benchmark_prices = benchmark_df['Close'],
    ma_period = 50
)

# Eval Comparative RS strategy vs. benchmark
rs_performance_df = evaluate_strategy(
    strategy_returns = rs_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Comparative Relative Strength (50-Day MA)',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
rs_eval_table = create_eval_table(rs_performance_df, 'Comparative Relative Strength (50-Day MA)')
rs_eval_table


GT(_tbl_data=                  Metric  Comparative Relative Strength (50-Day MA)  Benchmark
0           Total Return                                   5.076793   3.561391
1      Annualized Return                                   0.196617   0.181146
2  Annualized Volatility                                   0.153854   0.226756
3           Sharpe Ratio                                   1.277944   0.798860
4           Max Drawdown                                  -0.219726  -0.392813
5           Calmar Ratio                                   0.894826   0.461151
6         Daily Win Rate                                   0.547929   0.556052
7       Monthly Win Rate                                   0.633333   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3457b30>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Comparative Relative Strength (50-Day MA)', type=<ColInfoTypeEnum.default: 1>, column_label='Comparative Relative Strength (50-Day MA)', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b33dac60>, _spanners=Spanners([]), _heading=Heading(title='Comparative Relative Strength (50-Day MA)', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3456b10>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3456b70>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3457230>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3455d90>, <great_tables._gt_data.FormatInfo object at 0x7c28b3456ff0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False,

In [17]:
# Visualize Comparative RS strategy vs. benchmark
plot_equity_curves(rs_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Comparative Relative Strength (50-Day MA)')


### Trading Strategy 4: Supertrend - Shayan


In [18]:
# Define function to run Supertrend strategy
def run_supertrend_strategy(stock_dfs, atr_period=10, multiplier=3.0):
    """
    Executes a Supertrend strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when price is above the Supertrend line.
        - Sell (cash/flat position) when price is below the Supertrend line.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - atr_period (int): ATR period for Supertrend calculation. Default is 10.
        - multiplier (float): Multiplier for ATR in Supertrend calculation. Default is 3.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under Supertrend strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        high = df['High'].values
        low = df['Low'].values
        close = df['Close'].values
        n = len(df)

        prev_close = np.roll(close, 1)
        prev_close[0] = close[0]

        tr1 = high - low
        tr2 = np.abs(high - prev_close)
        tr3 = np.abs(low - prev_close)
        tr = np.maximum(tr1, np.maximum(tr2, tr3))

        atr = pd.Series(tr).ewm(alpha=1/atr_period, min_periods=atr_period).mean().to_numpy()

        hl2 = (high + low) / 2.0
        upperband = hl2 + multiplier * atr
        lowerband = hl2 - multiplier * atr

        final_upper = upperband.copy()
        final_lower = lowerband.copy()
        trend = np.ones(n, dtype=bool)

        for i in range(1, n):
            if close[i] > final_upper[i-1]:
                trend[i] = True
            elif close[i] < final_lower[i-1]:
                trend[i] = False
            else:
                trend[i] = trend[i-1]
                if trend[i] and final_lower[i] < final_lower[i-1]:
                    final_lower[i] = final_lower[i-1]
                if (not trend[i]) and final_upper[i] > final_upper[i-1]:
                    final_upper[i] = final_upper[i-1]

            if trend[i]:
                final_upper[i] = np.nan
            else:
                final_lower[i] = np.nan

        # Position: 1 = long, 0 = flat
        df['position'] = pd.Series(trend.astype(int), index=df.index).shift(1).fillna(0)

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute strategy returns
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [19]:
# Execute Supertrend strategy
supertrend_portfolio_returns = run_supertrend_strategy(stock_dfs, atr_period=10, multiplier=3.0)

# Eval Supertrend strategy vs. benchmark
supertrend_performance_df = evaluate_strategy(
    strategy_returns = supertrend_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Supertrend',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
supertrend_eval_table = create_eval_table(supertrend_performance_df, 'Supertrend')
supertrend_eval_table


GT(_tbl_data=                  Metric  Supertrend  Benchmark
0           Total Return    4.206439   3.561391
1      Annualized Return    0.180939   0.181146
2  Annualized Volatility    0.154967   0.226756
3           Sharpe Ratio    1.167599   0.798860
4           Max Drawdown   -0.284290  -0.392813
5           Calmar Ratio    0.636457   0.461151
6         Daily Win Rate    0.517059   0.556052
7       Monthly Win Rate    0.608333   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3b21b80>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Supertrend', type=<ColInfoTypeEnum.default: 1>, column_label='Supertrend', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b22ba0>, _spanners=Spanners([]), _heading=Heading(title='Supertrend', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3b23fe0>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3b21af0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3b22000>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3b22180>, <great_tables._gt_data.FormatInfo object at 0x7c28b3b21dc0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(

In [20]:
# Visualize Supertrend strategy vs. benchmark
plot_equity_curves(supertrend_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Supertrend')


### Trading Strategy 5: Rate of Change (ROC) - Shayan


In [21]:
# Define function to run ROC strategy
def run_roc_strategy(stock_dfs, lookback=20, threshold=0.0):
    """
    Executes a Rate of Change (ROC) strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when ROC > threshold.
        - Sell (cash/flat position) when ROC <= threshold.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - lookback (int): Lookback period for ROC calculation in days. Default is 20.
        - threshold (float): ROC threshold for signal generation. Default is 0.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under ROC strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        close = df['Close']
        roc = (close / close.shift(lookback) - 1.0) * 100

        # Position: 1 = long, 0 = flat
        df['position'] = (roc > threshold).astype(int).shift(1).fillna(0)

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute strategy returns
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [22]:
# Execute ROC strategy
roc_portfolio_returns = run_roc_strategy(stock_dfs, lookback=20, threshold=0.0)

# Eval ROC strategy vs. benchmark
roc_performance_df = evaluate_strategy(
    strategy_returns = roc_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'ROC',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
roc_eval_table = create_eval_table(roc_performance_df, 'ROC')
roc_eval_table


GT(_tbl_data=                  Metric       ROC  Benchmark
0           Total Return  5.168785   3.561391
1      Annualized Return  0.199528   0.181146
2  Annualized Volatility  0.162568   0.226756
3           Sharpe Ratio  1.227351   0.798860
4           Max Drawdown -0.254650  -0.392813
5           Calmar Ratio  0.783536   0.461151
6         Daily Win Rate  0.517872   0.556052
7       Monthly Win Rate  0.591667   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3a1c7d0>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='ROC', type=<ColInfoTypeEnum.default: 1>, column_label='ROC', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3a1c8c0>, _spanners=Spanners([]), _heading=Heading(title='ROC', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3a1c950>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3a1c710>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3a1c440>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3a1c380>, <great_tables._gt_data.FormatInfo object at 0x7c28b3a1c590>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='valu

In [23]:
# Visualize ROC strategy vs. benchmark
plot_equity_curves(roc_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'ROC')


### Trading Strategy 6: Volume-Weighted Momentum (VWM) - Shayan


In [24]:
# Define function to run VWM strategy
def run_vwm_strategy(stock_dfs, lookback=20, threshold=0.0):
    """
    Executes a Volume-Weighted Momentum (VWM) strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when VWM > threshold.
        - Sell (cash/flat position) when VWM <= threshold.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - lookback (int): Lookback period for momentum and volume calculation in days. Default is 20.
        - threshold (float): VWM threshold for signal generation. Default is 0.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under VWM strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        close = df['Close']
        vol = df['Volume']

        mom = close / close.shift(lookback) - 1
        vol_avg = vol.rolling(lookback).mean()
        vol_factor = vol / vol_avg
        vwm = mom * vol_factor

        # Position: 1 = long, 0 = flat
        df['position'] = (vwm > threshold).astype(int).shift(1).fillna(0)

        # Compute daily returns of underlying stock
        df['stock_return'] = df['Close'].pct_change()

        # Compute strategy returns
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Compute daily strategy return across portfolio, assuming equal allocation
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [25]:
# Execute VWM strategy
vwm_portfolio_returns = run_vwm_strategy(stock_dfs, lookback=20, threshold=0.0)

# Eval VWM strategy vs. benchmark
vwm_performance_df = evaluate_strategy(
    strategy_returns = vwm_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'VWM',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
vwm_eval_table = create_eval_table(vwm_performance_df, 'VWM')
vwm_eval_table


GT(_tbl_data=                  Metric       VWM  Benchmark
0           Total Return  5.168785   3.561391
1      Annualized Return  0.199528   0.181146
2  Annualized Volatility  0.162568   0.226756
3           Sharpe Ratio  1.227351   0.798860
4           Max Drawdown -0.254650  -0.392813
5           Calmar Ratio  0.783536   0.461151
6         Daily Win Rate  0.517872   0.556052
7       Monthly Win Rate  0.591667   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3b53560>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='VWM', type=<ColInfoTypeEnum.default: 1>, column_label='VWM', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b54fe0>, _spanners=Spanners([]), _heading=Heading(title='VWM', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3b53080>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3b539b0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3b53260>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3b52fc0>, <great_tables._gt_data.FormatInfo object at 0x7c28b3b535c0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_bottom_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_left_style=OptionsInfo(scss=True, category='table', type='valu

In [26]:
# Visualize VWM strategy vs. benchmark
plot_equity_curves(vwm_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'VWM')


### Trading Strategy 7: SMA Crossover (50/200) - Huzefa


In [27]:
# Define function to run SMA Crossover strategy
def run_sma_crossover_strategy(stock_dfs, short_window=50, long_window=200):
    """
    Executes an SMA Crossover strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when SMA_short > SMA_long.
        - Sell (cash/flat position) when SMA_short <= SMA_long.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - short_window (int): Lookback period for short SMA in days. Default is 50.
        - long_window (int): Lookback period for long SMA in days. Default is 200.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under SMA Crossover strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Use Close prices
        df['sma_short'] = df['Close'].rolling(window=short_window, min_periods=short_window).mean()
        df['sma_long']  = df['Close'].rolling(window=long_window, min_periods=long_window).mean()

        # Position: 1 = long, 0 = flat
        df['position'] = (df['sma_short'] > df['sma_long']).astype(int)

        # Underlying daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Strategy returns – use previous day's position to avoid look-ahead
        df['strategy_return'] = df['stock_return'] * df['position'].shift(1)

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict).dropna(how="all")

    # Equal-weight across all available stocks each day
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [28]:
# Execute SMA Crossover strategy
sma_crossover_portfolio_returns = run_sma_crossover_strategy(stock_dfs, short_window=50, long_window=200)

# Eval SMA Crossover strategy vs. benchmark
sma_crossover_performance_df = evaluate_strategy(
    strategy_returns = sma_crossover_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'SMA Crossover (50/200)',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
sma_crossover_eval_table = create_eval_table(sma_crossover_performance_df, 'SMA Crossover (50/200)')
sma_crossover_eval_table


GT(_tbl_data=                  Metric  SMA Crossover (50/200)  Benchmark
0           Total Return                7.689565   3.561391
1      Annualized Return                0.244033   0.181146
2  Annualized Volatility                0.212077   0.226756
3           Sharpe Ratio                1.150677   0.798860
4           Max Drawdown               -0.324585  -0.392813
5           Calmar Ratio                0.751830   0.461151
6         Daily Win Rate                0.508123   0.556052
7       Monthly Win Rate                0.650000   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3b93260>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='SMA Crossover (50/200)', type=<ColInfoTypeEnum.default: 1>, column_label='SMA Crossover (50/200)', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b22c30>, _spanners=Spanners([]), _heading=Heading(title='SMA Crossover (50/200)', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3b91610>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3b931a0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3b91670>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3b93e00>, <great_tables._gt_data.FormatInfo object at 0x7c28b3b914c0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value

In [29]:
# Visualize SMA Crossover strategy vs. benchmark
plot_equity_curves(sma_crossover_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'SMA Crossover (50/200)')


### Trading Strategy 8: Z-Score Mean Reversion - Huzefa


In [30]:
# Define function to run Z-Score Mean Reversion strategy
def run_zscore_strategy(stock_dfs, window=30, entry_threshold=1.5, exit_threshold=0.0):
    """
    Executes a Z-Score Mean Reversion strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy (long position) when z-score < -entry_threshold (oversold).
        - Sell (exit position) when z-score > -exit_threshold (mean reversion complete).

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - window (int): Lookback period for calculating rolling mean and std dev. Default is 30.
        - entry_threshold (float): Z-score threshold for entering position. Default is 1.5.
        - exit_threshold (float): Z-score threshold for exiting position. Default is 0.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under Z-Score Mean Reversion strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Calculate rolling mean and standard deviation
        df['rolling_mean'] = df['Close'].rolling(window=window, min_periods=window).mean()
        df['rolling_std'] = df['Close'].rolling(window=window, min_periods=window).std()

        # Calculate z-score
        df['zscore'] = (df['Close'] - df['rolling_mean']) / df['rolling_std']

        # Generate position signals with STATE MACHINE
        df['position'] = 0
        in_position = False

        for i in range(window, len(df)):  # Start after we have valid z-scores
            if not in_position:
                # Entry condition: z-score is very negative (oversold)
                if df['zscore'].iloc[i] < -entry_threshold:
                    df.loc[df.index[i], 'position'] = 1
                    in_position = True
                else:
                    df.loc[df.index[i], 'position'] = 0
            else:
                # Exit condition: z-score has reverted back toward mean
                if df['zscore'].iloc[i] > -exit_threshold:
                    df.loc[df.index[i], 'position'] = 0
                    in_position = False
                else:
                    # Hold position
                    df.loc[df.index[i], 'position'] = 1

        # Calculate underlying stock daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Strategy returns = position from previous day * today's stock return
        df['strategy_return'] = df['stock_return'] * df['position'].shift(1)

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict).dropna(how="all")

    # Equal-weight portfolio: average returns across all available stocks each day
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [31]:
# Execute Z-Score Mean Reversion strategy
zscore_portfolio_returns = run_zscore_strategy(stock_dfs, window=30, entry_threshold=1.5, exit_threshold=0.0)

# Eval Z-Score strategy vs. benchmark
zscore_performance_df = evaluate_strategy(
    strategy_returns = zscore_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Z-Score Mean Reversion',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
zscore_eval_table = create_eval_table(zscore_performance_df, 'Z-Score Mean Reversion')
zscore_eval_table


GT(_tbl_data=                  Metric  Z-Score Mean Reversion  Benchmark
0           Total Return                1.750970   3.561391
1      Annualized Return                0.116405   0.181146
2  Annualized Volatility                0.160129   0.226756
3           Sharpe Ratio                0.726946   0.798860
4           Max Drawdown               -0.216556  -0.392813
5           Calmar Ratio                0.537529   0.461151
6         Daily Win Rate                0.342811   0.556052
7       Monthly Win Rate                0.741667   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3a50e30>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Z-Score Mean Reversion', type=<ColInfoTypeEnum.default: 1>, column_label='Z-Score Mean Reversion', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3a503e0>, _spanners=Spanners([]), _heading=Heading(title='Z-Score Mean Reversion', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3a53fe0>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3a52b40>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3a50c50>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3a501a0>, <great_tables._gt_data.FormatInfo object at 0x7c28b3a504d0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value

In [32]:
# Visualize Z-Score Mean Reversion strategy vs. benchmark
plot_equity_curves(zscore_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Z-Score Mean Reversion')


### Trading Strategy 9: SMA + VADER Sentiment - Huzefa


In [33]:
# Initialize VADER sentiment analyzer
analyzer = SentimentIntensityAnalyzer()

def build_price_based_sentiment(df):
    """Create a simple daily sentiment score using VADER on text that describes each day's price move."""
    df = df.copy()
    df['daily_ret'] = df['Close'].pct_change()

    sentiment_values = []
    for r in df['daily_ret']:
        if pd.isna(r):
            sentiment_values.append(np.nan)
        else:
            text = f"The stock moved {r*100:.2f} percent today."
            score = analyzer.polarity_scores(text)['compound']
            sentiment_values.append(score)

    return pd.Series(sentiment_values, index=df.index)

# Define function to run SMA + VADER Sentiment strategy
def run_sma_vader_strategy(stock_dfs, short_window=50, long_window=200, sentiment_threshold=0.0):
    """
    Executes an SMA Crossover strategy filtered by VADER sentiment on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Compute SMA_short and SMA_long on Close prices.
        - Base trend signal: long when SMA_short > SMA_long, else flat.
        - Compute a daily VADER sentiment score (proxy based on price move).
        - Final position is long only when trend is bullish AND sentiment >= sentiment_threshold; otherwise flat.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - short_window (int): Lookback period for short SMA in days. Default is 50.
        - long_window (int): Lookback period for long SMA in days. Default is 200.
        - sentiment_threshold (float): Sentiment threshold for signal generation. Default is 0.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under SMA + VADER Sentiment strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Trend component: SMA crossover
        df['sma_short'] = df['Close'].rolling(window=short_window, min_periods=short_window).mean()
        df['sma_long'] = df['Close'].rolling(window=long_window, min_periods=long_window).mean()

        df['trend_long'] = (df['sma_short'] > df['sma_long']).astype(int)

        # Sentiment component (proxy using price-based text)
        df['sentiment'] = build_price_based_sentiment(df)

        # Sentiment filter: require sentiment >= threshold
        df['sentiment_long'] = (df['sentiment'] >= sentiment_threshold).astype(int)

        # Combined signal
        df['position'] = df['trend_long'] * df['sentiment_long']

        # Underlying daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Use previous day's position to avoid look-ahead bias
        df['strategy_return'] = df['stock_return'] * df['position'].shift(1)

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict).dropna(how="all")

    # Equal-weight portfolio
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns


In [34]:
# Execute SMA + VADER Sentiment strategy
sma_vader_portfolio_returns = run_sma_vader_strategy(stock_dfs, short_window=50, long_window=200, sentiment_threshold=0.0)

# Eval SMA + VADER strategy vs. benchmark
sma_vader_performance_df = evaluate_strategy(
    strategy_returns = sma_vader_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'SMA + VADER Sentiment',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
sma_vader_eval_table = create_eval_table(sma_vader_performance_df, 'SMA + VADER Sentiment')
sma_vader_eval_table


GT(_tbl_data=                  Metric  SMA + VADER Sentiment  Benchmark
0           Total Return               7.689565   3.561391
1      Annualized Return               0.244033   0.181146
2  Annualized Volatility               0.212077   0.226756
3           Sharpe Ratio               1.150677   0.798860
4           Max Drawdown              -0.324585  -0.392813
5           Calmar Ratio               0.751830   0.461151
6         Daily Win Rate               0.508123   0.556052
7       Monthly Win Rate               0.650000   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3a1f860>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='SMA + VADER Sentiment', type=<ColInfoTypeEnum.default: 1>, column_label='SMA + VADER Sentiment', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b92900>, _spanners=Spanners([]), _heading=Heading(title='SMA + VADER Sentiment', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3a299a0>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3a29d90>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3a2b9b0>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3a29a60>, <great_tables._gt_data.FormatInfo object at 0x7c28b3a29820>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), tab

In [35]:
# Visualize SMA + VADER Sentiment strategy vs. benchmark
plot_equity_curves(sma_vader_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'SMA + VADER Sentiment')


### Trading Strategy 10: RSI Oversold/Overbought - Stock Trading Strategies


### Trading Strategy 10: RSI Oversold/Overbought - Stock Trading Strategies

In [36]:
# Define function to run RSI strategy
def run_rsi_strategy(stock_dfs, rsi_period=14, oversold=30, overbought=70):
    """
    Executes an RSI Oversold/Overbought strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy when RSI < oversold (oversold).
        - Sell (exit) when RSI > overbought (overbought).

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - rsi_period (int): Period for RSI calculation. Default is 14.
        - oversold (float): RSI level considered oversold. Default is 30.
        - overbought (float): RSI level considered overbought. Default is 70.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under RSI strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Compute RSI
        df['RSI14'] = ta.rsi(df['Close'], length=rsi_period)

        # Generate signals
        df['buy_signal'] = (df['RSI14'] < oversold).astype(int)
        df['sell_signal'] = (df['RSI14'] > overbought).astype(int)

        # Create position: +1 when long, 0 when in cash
        df['position'] = 0

        # Forward-fill position based on signals
        for i in range(1, len(df)):
            if df['buy_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 1
            elif df['sell_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 0
            else:
                df.iloc[i, df.columns.get_loc('position')] = df['position'].iloc[i-1]

        # Avoid look-ahead bias by shifting positions by 1 day
        df['position'] = df['position'].shift(1).fillna(0)

        # Compute stock daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Strategy return = daily_return * position
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Equal weights across all holdings
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns

In [37]:
# Execute RSI strategy
rsi_portfolio_returns = run_rsi_strategy(stock_dfs, rsi_period=14, oversold=30, overbought=70)

# Eval RSI strategy vs. benchmark
rsi_performance_df = evaluate_strategy(
    strategy_returns = rsi_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'RSI Oversold/Overbought',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
rsi_eval_table = create_eval_table(rsi_performance_df, 'RSI Oversold/Overbought')
rsi_eval_table

GT(_tbl_data=                  Metric  RSI Oversold/Overbought  Benchmark
0           Total Return                 1.448646   3.561391
1      Annualized Return                 0.104037   0.181146
2  Annualized Volatility                 0.157665   0.226756
3           Sharpe Ratio                 0.659859   0.798860
4           Max Drawdown                -0.319837  -0.392813
5           Calmar Ratio                 0.325280   0.461151
6         Daily Win Rate                 0.441105   0.556052
7       Monthly Win Rate                 0.633333   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3a3f7d0>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='RSI Oversold/Overbought', type=<ColInfoTypeEnum.default: 1>, column_label='RSI Oversold/Overbought', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3bf3ef0>, _spanners=Spanners([]), _heading=Heading(title='RSI Oversold/Overbought', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3a3f530>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3a3f890>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3a3f800>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3a3f2c0>, <great_tables._gt_data.FormatInfo object at 0x7c28b3a3ea20>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type

In [38]:
# Visualize RSI strategy vs. benchmark
plot_equity_curves(rsi_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'RSI Oversold/Overbought')

### Trading Strategy 11: Donchian Channel Breakout - Stock Trading Strategies

In [39]:
# Define function to run Donchian Channel Breakout strategy
def run_donchian_strategy(stock_dfs, lookback=20):
    """
    Executes a Donchian Channel Breakout strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy when stock price breaks above the lookback-day upper band.
        - Sell when price breaks below the lookback-day lower band.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - lookback (int): Lookback period for Donchian Channel. Default is 20.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under Donchian Channel Breakout strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Compute Donchian Channels
        df['donchian_upper'] = df['High'].rolling(lookback).max()
        df['donchian_lower'] = df['Low'].rolling(lookback).min()

        # Generate breakout signals
        df['buy_signal'] = (df['Close'] > df['donchian_upper']).astype(int)
        df['sell_signal'] = (df['Close'] < df['donchian_lower']).astype(int)

        # Position: +1 when long, 0 when in cash
        df['position'] = 0

        for i in range(1, len(df)):
            if df['buy_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 1
            elif df['sell_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 0
            else:
                df.iloc[i, df.columns.get_loc('position')] = df['position'].iloc[i-1]

        # Shift by 1 day to avoid look-ahead bias
        df['position'] = df['position'].shift(1).fillna(0)

        # Daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Strategy return
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Equal-weight portfolio
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns

In [40]:
# Execute Donchian Channel Breakout strategy
donchian_portfolio_returns = run_donchian_strategy(stock_dfs, lookback=20)

# Eval Donchian strategy vs. benchmark
donchian_performance_df = evaluate_strategy(
    strategy_returns = donchian_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Donchian Channel Breakout',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
donchian_eval_table = create_eval_table(donchian_performance_df, 'Donchian Channel Breakout')
donchian_eval_table

GT(_tbl_data=                  Metric  Donchian Channel Breakout  Benchmark
0           Total Return                        0.0   3.561391
1      Annualized Return                        0.0   0.181146
2  Annualized Volatility                        0.0   0.226756
3           Sharpe Ratio                        NaN   0.798860
4           Max Drawdown                        0.0  -0.392813
5           Calmar Ratio                        NaN   0.461151
6         Daily Win Rate                        0.0   0.556052
7       Monthly Win Rate                        0.0   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28b3a53cb0>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Donchian Channel Breakout', type=<ColInfoTypeEnum.default: 1>, column_label='Donchian Channel Breakout', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b533e0>, _spanners=Spanners([]), _heading=Heading(title='Donchian Channel Breakout', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b3b23e30>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b3b23da0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b3a8c530>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b3b236b0>, <great_tables._gt_data.FormatInfo object at 0x7c28b3a8c9b0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True

In [41]:
# Visualize Donchian Channel Breakout strategy vs. benchmark
plot_equity_curves(donchian_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Donchian Channel Breakout')

### Trading Strategy 12: Bollinger Band Reversal - Stock Trading Strategies

In [42]:
# Define function to run Bollinger Band Reversal strategy
def run_bollinger_strategy(stock_dfs, lookback=20, num_std=2.0):
    """
    Executes a Bollinger Band Reversal strategy on a dictionary of stock DataFrames.

    Strategy:
    ---------
        - Buy when price touches or falls below the lower Bollinger Band.
        - Sell when price reaches or rises above the upper Bollinger Band.

    Parameters:
    -----------
        - stock_dfs (dict): Dictionary of DataFrames containing historical stock price data keyed by ticker.
        - lookback (int): Lookback period for Bollinger Bands. Default is 20.
        - num_std (float): Number of standard deviations for bands. Default is 2.0.

    Returns:
    --------
        - pd.Series: Daily returns of equal-weighted portfolio under Bollinger Band Reversal strategy.
    """

    # Initialize dict to store strategy daily returns for each stock
    strategy_returns_dict = {}

    # Iterate through each stock
    for ticker, df in stock_dfs.items():
        df = df.copy()

        # Compute Bollinger Bands
        df['bb_middle'] = df['Close'].rolling(lookback).mean()
        df['bb_std'] = df['Close'].rolling(lookback).std()
        df['bb_upper'] = df['bb_middle'] + num_std * df['bb_std']
        df['bb_lower'] = df['bb_middle'] - num_std * df['bb_std']

        # Generate reversal signals
        df['buy_signal'] = (df['Close'] <= df['bb_lower']).astype(int)
        df['sell_signal'] = (df['Close'] >= df['bb_upper']).astype(int)

        # Position variable
        df['position'] = 0

        for i in range(1, len(df)):
            if df['buy_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 1
            elif df['sell_signal'].iloc[i] == 1:
                df.iloc[i, df.columns.get_loc('position')] = 0
            else:
                df.iloc[i, df.columns.get_loc('position')] = df['position'].iloc[i-1]

        # Avoid look-ahead bias
        df['position'] = df['position'].shift(1).fillna(0)

        # Daily returns
        df['stock_return'] = df['Close'].pct_change()

        # Strategy returns
        df['strategy_return'] = df['stock_return'] * df['position']

        # Store result in dict
        strategy_returns_dict[ticker] = df['strategy_return']

    # Combine strategy returns for each stock into single df for portfolio aggregation
    portfolio_df = pd.DataFrame(strategy_returns_dict)

    # Equal-weight portfolio
    portfolio_daily_returns = portfolio_df.mean(axis=1)

    return portfolio_daily_returns

In [43]:
# Execute Bollinger Band Reversal strategy
bollinger_portfolio_returns = run_bollinger_strategy(stock_dfs, lookback=20, num_std=2.0)

# Eval Bollinger Band Reversal strategy vs. benchmark
bollinger_performance_df = evaluate_strategy(
    strategy_returns = bollinger_portfolio_returns,
    benchmark_returns = benchmark_df['benchmark_daily_return'],
    strategy_name = 'Bollinger Band Reversal',
    trading_days = 252,
    risk_free_rate = 0.0
)

# Display formatted table
bollinger_eval_table = create_eval_table(bollinger_performance_df, 'Bollinger Band Reversal')
bollinger_eval_table

GT(_tbl_data=                  Metric  Bollinger Band Reversal  Benchmark
0           Total Return                 3.089571   3.561391
1      Annualized Return                 0.161998   0.181146
2  Annualized Volatility                 0.188680   0.226756
3           Sharpe Ratio                 0.858587   0.798860
4           Max Drawdown                -0.303785  -0.392813
5           Calmar Ratio                 0.533268   0.461151
6         Daily Win Rate                 0.480504   0.556052
7       Monthly Win Rate                 0.733333   0.675000, _body=<great_tables._gt_data.Body object at 0x7c28e576f740>, _boxhead=Boxhead([ColInfo(var='Metric', type=<ColInfoTypeEnum.default: 1>, column_label='Metric', column_align='left', column_width=None), ColInfo(var='Bollinger Band Reversal', type=<ColInfoTypeEnum.default: 1>, column_label='Bollinger Band Reversal', column_align='right', column_width=None), ColInfo(var='Benchmark', type=<ColInfoTypeEnum.default: 1>, column_label='Benchmark', column_align='right', column_width=None)]), _stub=<great_tables._gt_data.Stub object at 0x7c28b3b91100>, _spanners=Spanners([]), _heading=Heading(title='Bollinger Band Reversal', subtitle='Strategy Performance vs. Benchmark', preheader=None), _stubhead=None, _summary_rows=<great_tables._gt_data.SummaryRows object at 0x7c28b397caa0>, _summary_rows_grand=<great_tables._gt_data.SummaryRows object at 0x7c28b397c9b0>, _source_notes=[], _footnotes=[], _styles=[], _locale=<great_tables._gt_data.Locale object at 0x7c28b397cd40>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7c28b397c260>, <great_tables._gt_data.FormatInfo object at 0x7c28b397c2c0>], _substitutions=[], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_additional_css=OptionsInfo(scss=False, category='table', type='values', value=[]), table_font_names=OptionsInfo(scss=False, category='table', type='values', value=['-apple-system', 'BlinkMacSystemFont', 'Segoe UI', 'Roboto', 'Oxygen', 'Ubuntu', 'Cantarell', 'Helvetica Neue', 'Fira Sans', 'Droid Sans', 'Arial', 'sans-serif']), table_font_size=OptionsInfo(scss=True, category='table', type='px', value='16px'), table_font_weight=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_style=OptionsInfo(scss=True, category='table', type='value', value='normal'), table_font_color=OptionsInfo(scss=True, category='table', type='value', value='#333333'), table_font_color_light=OptionsInfo(scss=True, category='table', type='value', value='#FFFFFF'), table_border_top_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_top_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_top_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_top_color=OptionsInfo(scss=True, category='table', type='value', value='#A8A8A8'), table_border_right_style=OptionsInfo(scss=True, category='table', type='value', value='none'), table_border_right_width=OptionsInfo(scss=True, category='table', type='px', value='2px'), table_border_right_color=OptionsInfo(scss=True, category='table', type='value', value='#D3D3D3'), table_border_bottom_include=OptionsInfo(scss=False, category='table', type='boolean', value=True), table_border_bottom_style=OptionsInfo(scss=True, category='table', type='value', value='solid'), table_border_bottom_width=OptionsInfo(scss=True, category='table', type

In [44]:
# Visualize Bollinger Band Reversal strategy vs. benchmark
plot_equity_curves(bollinger_portfolio_returns, benchmark_df['benchmark_daily_return'], strategy_name = 'Bollinger Band Reversal')